## Make a program to choose randomly p fraction of the population to infect initially
* Randomly with choosen probability picks 0 and 1 
* We find list of all unique users and then we need to infect a percentage of population
* Again a problem here is that we need to start infecting users only after a particular time
* we need to make this set to be positive or negative

**I propose that there could be atleast two mechanism to start infection**
1. Randomly infect people by choosing them after a particular time
2. Randomly infect people by choosing a particular place at particular time (this is how COVID started)
3. If choosing step 2 then we can randmly infect people who were at that place at a particular time
4. Using alpha as infection rate

In [1]:
import pandas as pd

df = pd.read_csv("processedTMSC2014.tsv",sep='\t', engine="python")
df.drop(["Unnamed: 0"],axis=1, inplace=True)

Import the ArcGIS API for Python. This adds a GeoAccessor and spatially enables your DataFrame objects. As you will see in this notebook, you can then easily plot your data both as charts and as maps.

In [2]:
import matplotlib.pyplot as plt
%matplotlib inline

from arcgis.gis import GIS
from arcgis.features import GeoAccessor, GeoSeriesAccessor

/opt/anaconda3/envs/cs293b/lib/python3.7/site-packages/arcgis/features/_data/geodataset/utils.py:15: FutureWarning: The pandas.datetime class is deprecated and will be removed from pandas in a future version. Import from datetime module instead.
  pd.datetime,


# EXTRA IDEAS
## We can use venue catorgories to define the probabilty of infection
* If it is a closed space we can have more probability 
* If it is public space which is frequented by many we can give more probability
* Also we can give probability of contamination by looking at how many people were there at the place at given time

In [3]:
df

User ID (anonymized)     Venue ID (Foursquare)  \
0                        470  49bbd6c0f964a520f4531fe3   
1                        979  4a43c0aef964a520c6a61fe3   
2                         69  4c5cc7b485a1e21e00d35711   
3                        395  4bc7086715a7ef3bef9878da   
4                         87  4cf2c5321d18a143951b5cec   
...                      ...                       ...   
227423                   688  3fd66200f964a52000e71ee3   
227424                   560  4bca32ff0687ef3be789dbcc   
227425                   945  50a77716e4b0b5a9492f6f56   
227426                   671  4514efe0f964a520e7391fe3   
227427                   942  4a1e0ca0f964a520bf7b1fe3   

       Venue category ID (Foursquare) Venue category name (Fousquare)  \
0            4bf58dd8d48988d127951735             Arts & Crafts Store   
1            4bf58dd8d48988d1df941735                          Bridge   
2            4bf58dd8d48988d103941735                  Home (private)   
3            4bf58dd8d48988d104941735                  Medical Center   
4            4bf58dd8d48988d1cb941735                      Food Truck   
...                               ...                             ...   
227423       4bf58dd8d48988d1e7931735                     Music Venue   
227424       4bf58dd8d48988d16c941735                    Burger Joint   
227425       4bf58dd8d48988d103941735                  Home (private)   
227426       4bf58dd8d48988d11d941735                             Bar   
227427       4bf58dd8d48988d116941735                             Bar   

         Latitude  Longitude  Timezone offset(minutes)  \
0       40.719810 -74.002581                      -240   
1       40.606800 -74.044170                      -240   
2       40.716162 -73.883070                      -240   
3       40.745164 -73.982519                      -240   
4       40.740104 -73.989658                      -240   
...           ...        ...                       ...   
227423  40.733596 -74.003139                      -300   
227424  40.745719 -73.993720                      -300   
227425  40.854364 -73.883070                      -300   
227426  40.735981 -74.029309                      -300   
227427  40.726805 -73.957422                      -300   

                              UTC time  Status  Iteration  InfectorId  \
0       Tue Apr 03 18:00:09 +0000 2012       0          0           0   
1       Tue Apr 03 18:00:25 +0000 2012       0          0           0   
2       Tue Apr 03 18:02:24 +0000 2012       0          0           0   
3       Tue Apr 03 18:02:41 +0000 2012       0          0           0   
4       Tue Apr 03 18:03:00 +0000 2012       0          0           0   
...                                ...     ...        ...         ...   
227423  Sat Feb 16 02:29:11 +0000 2013       0          0           0   
227424  Sat Feb 16 02:31:35 +0000 2013       0          0           0   
227425  Sat Feb 16 02:33:16 +0000 2013       0          0           0   
227426  Sat Feb 16 02:34:31 +0000 2013       0          0           0   
227427  Sat Feb 16 02:35:36 +0000 2013       0          0           0   

        InfectionTime        Time  
0                   0  1333476009  
1                   0  1333476025  
2                   0  1333476144  
3                   0  1333476161  
4                   0  1333476180  
...               ...         ...  
227423              0  1360981751  
227424              0  1360981895  
227425              0  1360981996  
227426              0  1360982071  
227427              0  1360982136  

[227428 rows x 13 columns]

# We set the randomly chosen population to be infected

In [4]:
import numpy as np

alpha = 0.1

#choosing unique users from list of all user IDs
unique_users =  pd.unique(df["User ID (anonymized)"])#.

print(f"Number of unique users are: {len(unique_users)}")

# this is when we are infecting people after a particular time
gen_positive = np.random.choice((1,0),size = len(unique_users), p=[alpha, 1-alpha])

#Choosing the time at which infection begins
infect_time = df.iloc[2000]["Time"]

infections = np.sum(gen_positive)
print(f"Number of infected users: {infections}")

Number of unique users are: 1083
Number of infected users: 117


In [5]:
#Query logic to select only those users whose user id and time matches or  those who are positive already
for i in range(len(unique_users)):
    #print(i)
    if gen_positive[i] == 1:
        #Below query gives sets status to 1 if infected userId and time condition matches
        df["Status"]= np.where( ( (df["User ID (anonymized)"] == unique_users[i]) & (df["Time"] >= infect_time) ) | (df["Status"] == 1),1,0)

# Setting infection time for all
df["InfectionTime"] = np.where(df["Status"]==1,infect_time,0)

count_infected = len(df[df["Status"]==1])
print(f"number of infect rows: {count_infected}")

number of infect rows: 22774


In [6]:
df

User ID (anonymized)     Venue ID (Foursquare)  \
0                        470  49bbd6c0f964a520f4531fe3   
1                        979  4a43c0aef964a520c6a61fe3   
2                         69  4c5cc7b485a1e21e00d35711   
3                        395  4bc7086715a7ef3bef9878da   
4                         87  4cf2c5321d18a143951b5cec   
...                      ...                       ...   
227423                   688  3fd66200f964a52000e71ee3   
227424                   560  4bca32ff0687ef3be789dbcc   
227425                   945  50a77716e4b0b5a9492f6f56   
227426                   671  4514efe0f964a520e7391fe3   
227427                   942  4a1e0ca0f964a520bf7b1fe3   

       Venue category ID (Foursquare) Venue category name (Fousquare)  \
0            4bf58dd8d48988d127951735             Arts & Crafts Store   
1            4bf58dd8d48988d1df941735                          Bridge   
2            4bf58dd8d48988d103941735                  Home (private)   
3            4bf58dd8d48988d104941735                  Medical Center   
4            4bf58dd8d48988d1cb941735                      Food Truck   
...                               ...                             ...   
227423       4bf58dd8d48988d1e7931735                     Music Venue   
227424       4bf58dd8d48988d16c941735                    Burger Joint   
227425       4bf58dd8d48988d103941735                  Home (private)   
227426       4bf58dd8d48988d11d941735                             Bar   
227427       4bf58dd8d48988d116941735                             Bar   

         Latitude  Longitude  Timezone offset(minutes)  \
0       40.719810 -74.002581                      -240   
1       40.606800 -74.044170                      -240   
2       40.716162 -73.883070                      -240   
3       40.745164 -73.982519                      -240   
4       40.740104 -73.989658                      -240   
...           ...        ...                       ...   
227423  40.733596 -74.003139                      -300   
227424  40.745719 -73.993720                      -300   
227425  40.854364 -73.883070                      -300   
227426  40.735981 -74.029309                      -300   
227427  40.726805 -73.957422                      -300   

                              UTC time  Status  Iteration  InfectorId  \
0       Tue Apr 03 18:00:09 +0000 2012       0          0           0   
1       Tue Apr 03 18:00:25 +0000 2012       0          0           0   
2       Tue Apr 03 18:02:24 +0000 2012       0          0           0   
3       Tue Apr 03 18:02:41 +0000 2012       0          0           0   
4       Tue Apr 03 18:03:00 +0000 2012       0          0           0   
...                                ...     ...        ...         ...   
227423  Sat Feb 16 02:29:11 +0000 2013       0          0           0   
227424  Sat Feb 16 02:31:35 +0000 2013       0          0           0   
227425  Sat Feb 16 02:33:16 +0000 2013       0          0           0   
227426  Sat Feb 16 02:34:31 +0000 2013       0          0           0   
227427  Sat Feb 16 02:35:36 +0000 2013       0          0           0   

        InfectionTime        Time  
0                   0  1333476009  
1                   0  1333476025  
2                   0  1333476144  
3                   0  1333476161  
4                   0  1333476180  
...               ...         ...  
227423              0  1360981751  
227424              0  1360981895  
227425              0  1360981996  
227426              0  1360982071  
227427              0  1360982136  

[227428 rows x 13 columns]

# We need to do following
* We need to find every person that has been infected
* for every person that has been infected we need to find the other person who was at same place and time range
* infect these people with certain probability


    print(f"Meeting population for \n{infector}")
    print(meeting_population, i)
    for j in range(0,len(meeting_population)):
        person = df.iloc[meeting_population[j]]
        if(person["Status"]==0):
            print("Non infected person met.................")
            if( person["Time"] >= infector["Time"] and person["Time"]<= infector["Time"]+3600):
                print("In range.............................")
                #Find all the entries of this person after this time and set details
                person_rows = list(np.where((df["User ID (anonymized)"]==person["User ID (anonymized)"]) & (df["Time"]>=person["Time"]))[0])
                print("Places where this person has rows")
                print(person_rows)
                for k in range(len(person_rows)):
                    df.iloc[meeting_population[j]]["Status"] = 1
                    df.iloc[meeting_population[j]]["InfectorId"] = infector["User ID (anonymized)"]
                    df.iloc[meeting_population[j]]["InfectionTime"] = person["Time"]
            else:
                print("Saved! Was not in time range of 1 hours for infection")
        else:
            # It might so happen that 1st infector was not processed to infect first
            if( person["Time"] >= infector["Time"] and person["Time"]<= infector["Time"]+3600):
                print("In range.............................")
          
                if(person["InfectionTime"] >= person["Time"]):
                    print("Infected already........")
                else:
                    #Find all the entries of this person after this time and set details
                    print("Updating new infector.....................")
                    person_rows = list(np.where((df["User ID (anonymized)"]==person["User ID (anonymized)"]) & (df["Time"]>=person["Time"]))[0])
                    print("Places where this person has rows")
                    print(person_rows)
                    for k in range(len(person_rows)):
                        df.iloc[meeting_population[j]]["Status"] = 1
                        df.iloc[meeting_population[j]]["InfectorId"] = infector["User ID (anonymized)"]
                        df.iloc[meeting_population[j]]["InfectionTime"] = person["Time"]
            else:
                print("Saved! Was not in time range of 1 hours for infection")
    

In [7]:
# Find all the infected rows
infected_users_dataframe = df[df["Status"]==1]
print("List of infected users")
infected_users_dataframe

List of infected users


User ID (anonymized)     Venue ID (Foursquare)  \
1999                     503  4ea073e3cc21b2fa8ecb3a6e   
2001                     503  4d6d976d792bb60cbdd156be   
2002                     666  4a8108a0f964a52095f61fe3   
2013                     601  40b68100f964a5207d001fe3   
2036                    1071  4a525e9df964a52094b11fe3   
...                      ...                       ...   
227380                   314  50c3cbbce4b085c8e4119be8   
227381                   875  49f47a7af964a5200a6b1fe3   
227397                   542  4be1db7dedbb0f47c5eaa615   
227415                   737  4a73515ef964a5201edc1fe3   
227416                   751  41005500f964a5204e0b1fe3   

       Venue category ID (Foursquare) Venue category name (Fousquare)  \
1999         4bf58dd8d48988d162941735            Other Great Outdoors   
2001         4bf58dd8d48988d1c1941735              Mexican Restaurant   
2002         4bf58dd8d48988d176941735            Gym / Fitness Center   
2013         4bf58dd8d48988d163941735                            Park   
2036         4bf58dd8d48988d121941735                             Bar   
...                               ...                             ...   
227380       4d954b0ea243a5684a65b473               Convenience Store   
227381       4bf58dd8d48988d120941735                             Bar   
227397       4bf58dd8d48988d1a3941735       College Academic Building   
227415       4bf58dd8d48988d1f8941735          Furniture / Home Store   
227416       4bf58dd8d48988d116941735                             Bar   

         Latitude  Longitude  Timezone offset(minutes)  \
1999    40.642926 -74.014155                      -240   
2001    40.641934 -74.013622                      -240   
2002    40.762959 -73.915591                      -240   
2013    40.742188 -73.987924                      -240   
2036    40.754018 -73.984532                      -240   
...           ...        ...                       ...   
227380  40.749021 -74.136357                      -300   
227381  40.749443 -73.984865                      -300   
227397  40.776677 -73.980567                      -300   
227415  40.715722 -74.011751                      -300   
227416  40.666674 -73.988171                      -300   

                              UTC time  Status  Iteration  InfectorId  \
1999    Wed Apr 04 17:17:34 +0000 2012       1          0           0   
2001    Wed Apr 04 17:17:54 +0000 2012       1          0           0   
2002    Wed Apr 04 17:18:21 +0000 2012       1          0           0   
2013    Wed Apr 04 17:25:03 +0000 2012       1          0           0   
2036    Wed Apr 04 17:34:22 +0000 2012       1          0           0   
...                                ...     ...        ...         ...   
227380  Sat Feb 16 01:42:05 +0000 2013       1          0           0   
227381  Sat Feb 16 01:43:57 +0000 2013       1          0           0   
227397  Sat Feb 16 02:02:48 +0000 2013       1          0           0   
227415  Sat Feb 16 02:18:49 +0000 2013       1          0           0   
227416  Sat Feb 16 02:19:07 +0000 2013       1          0           0   

        InfectionTime        Time  
1999       1333559854  1333559854  
2001       1333559854  1333559874  
2002       1333559854  1333559901  
2013       1333559854  1333560303  
2036       1333559854  1333560862  
...               ...         ...  
227380     1333559854  1360978925  
227381     1333559854  1360979037  
227397     1333559854  1360980168  
227415     1333559854  1360981129  
227416     1333559854  1360981147  

[22774 rows x 13 columns]

In [8]:
# Find all the infected users
infected_users_dataframe = df[df["Status"]==1]
infected_users = pd.unique(infected_users_dataframe["User ID (anonymized)"])
print("Infected Users are: ")
print(infected_users)
#count number of infections
infections = len(infected_users)
print(f"Total infections are: {infections}")
# Infection list stores list of infected people per round of simulation
infection_list = []
infection_list.append(infected_users)
# We need to find all the users who where at the same place as the infected user and in time range of 1 hrs
# 1hr = 3600 seconds
# ITERATING OVER ALL ROWS AND CHECKING TIME
iteration_count = 0
while(infections!=0):
    # we will maintain this variable to fetch inly new infections
    print("#############################################################################")
    print("#############################################################################")
    print("#############################################################################")
    infected_rows = len(infected_users_dataframe)
    for i in range(infected_rows):
        print(f"Calculating for infected person: {i} of {infected_rows}")
        infector = infected_users_dataframe.iloc[i]
        
        ##print("Infector is:")
        ##print("###################################################################")
        ##print(infector)
        ##print("###################################################################")
        
        # Finding all those prople infector meets after start of infection time
        # meeting_population =  list(np.where( (df["Latitude"] == infector["Latitude"]) & (df["Longitude"] == infector["Longitude"])  & (df["Time"] >= infect_time))[0])
        
        # Finding all people that infector meets at infectors time range
        # Meeting Population is the list of indices of the people, not the User Id (anonymized)
        # We are keeping 3 hours time window -1 +2
        
        meeting_population =  list(np.where( (df["Latitude"] == infector["Latitude"]) & (df["Longitude"] == infector["Longitude"]) & ( (df["Time"] >= (infector["Time"]-3600)) & (df["Time"] <= (infector["Time"]+7200)) ))[0])
        
        print("List of people this infector meets: "+str({len(meeting_population)})) 
        ##print(meeting_population)
        ##print(meeting_population)
        
        for index in meeting_population:
            person = df.iloc[index]
            if(person["Status"]==0):
                
                print(f"Non infected person met.................{index}")
                ##print("In range.............................")
                #Find all the entries of this person after this time and set details
                
                person_rows = np.where( (df["User ID (anonymized)"]==person["User ID (anonymized)"]) & (df["Time"]>=person["Time"]))[0]
                
                ##print("Places where this person has rows")
                ##print(f"Rows of person is : {len(person_rows)}")
                
                # TO MAKE MORE EFFIECIENT
                # https://stackoverflow.com/questions/49447233/python-maintain-multiple-columns-with-np-where
                for k in range(len(person_rows)):
                    df.at[index, "Status"] = 1
                    #print("Status Set")
                    df.at[index, "InfectorId"] = infector["User ID (anonymized)"]
                    #print("Infector Id Set")
                    df.at[index, "InfectionTime"] = person["Time"]
                    #print("Infection Time Set")
                    df.at[index, "Iteration"] = iteration_count+1
                    df.at[index, "InfectionLongitude"] = infector["Longitude"]
                    df.at[index, "InfectionLatitude"] = infector["Latitude"]
            else:
                # AS data is sorted with time we assume that we don't need tp bother who infects first
                print(f"Met with an already infected person.................{index}")
                
    # Find all the infected users
    # HERE WE MUST ALSO SET CONDITIONS BASED ON ITERATION, FETCH ONLY THAT WERE INFECTED IN THIS ITERATION
    iteration_count += 1
    print("Finding new Infections............................")
    infected_users_dataframe = df[(df["Status"]==1) & (df["Iteration"]==iteration_count)]
    infected_users = pd.unique(infected_users_dataframe["User ID (anonymized)"])
    infection_list.append(infected_users)
    ##print("Infected Users are: ")
    ##print(infected_users)
    #count number of infections
    print("Infected Users are: ")
    print(infected_users)
    infections = len(infected_users)
    print(f"Total new infections are: {infections}") 
    print("#############################################################################")
    print("#############################################################################")
    print("#############################################################################")

Infected Users are: 
[ 503  666  601 1071  615  217  314  397  316  315  481  221  563  894
  751   54   65  195   46  438  371 1013  874  941  564  169 1042  328
  198  906 1002  300  433  834  265  207  598 1009   10   61  391  540
  377  478  541 1080  507  376  241  310  116  705  403  261  309   40
  176  624  744  226  491  251 1028  284  737  777  330  897  108  132
  332 1011  973  361  295  695 1069  974  953  203 1033  745   94  453
   18  175  859  269  466   42  929  385  326   31 1004  442  447  748
  490  928  932  583  137  676  875   41  821  595  165  960  761  743
  488 1035  542  587    6]
Total infections are: 117
#############################################################################
#############################################################################
#############################################################################
Calculating for infected person: 0 of 22774
List of people this infector meets: {1}
Met with an already infected person.....

List of people this infector meets: {1}
Met with an already infected person.................2440
Calculating for infected person: 58 of 22774
List of people this infector meets: {1}
Met with an already infected person.................2441
Calculating for infected person: 59 of 22774
List of people this infector meets: {1}
Met with an already infected person.................2443
Calculating for infected person: 60 of 22774
List of people this infector meets: {1}
Met with an already infected person.................2455
Calculating for infected person: 61 of 22774
List of people this infector meets: {1}
Met with an already infected person.................2460
Calculating for infected person: 62 of 22774
List of people this infector meets: {1}
Met with an already infected person.................2468
Calculating for infected person: 63 of 22774
List of people this infector meets: {1}
Met with an already infected person.................2476
Calculating for infected person: 64 of 22774
List o

List of people this infector meets: {1}
Met with an already infected person.................3145
Calculating for infected person: 125 of 22774
List of people this infector meets: {1}
Met with an already infected person.................3150
Calculating for infected person: 126 of 22774
List of people this infector meets: {1}
Met with an already infected person.................3171
Calculating for infected person: 127 of 22774
List of people this infector meets: {1}
Met with an already infected person.................3213
Calculating for infected person: 128 of 22774
List of people this infector meets: {1}
Met with an already infected person.................3214
Calculating for infected person: 129 of 22774
List of people this infector meets: {1}
Met with an already infected person.................3245
Calculating for infected person: 130 of 22774
List of people this infector meets: {1}
Met with an already infected person.................3253
Calculating for infected person: 131 of 22774

Calculating for infected person: 174 of 22774
List of people this infector meets: {1}
Met with an already infected person.................3674
Calculating for infected person: 175 of 22774
List of people this infector meets: {1}
Met with an already infected person.................3683
Calculating for infected person: 176 of 22774
List of people this infector meets: {1}
Met with an already infected person.................3691
Calculating for infected person: 177 of 22774
List of people this infector meets: {1}
Met with an already infected person.................3692
Calculating for infected person: 178 of 22774
List of people this infector meets: {1}
Met with an already infected person.................3701
Calculating for infected person: 179 of 22774
List of people this infector meets: {1}
Met with an already infected person.................3718
Calculating for infected person: 180 of 22774
List of people this infector meets: {1}
Met with an already infected person.................3721

List of people this infector meets: {1}
Met with an already infected person.................4274
Calculating for infected person: 236 of 22774
List of people this infector meets: {1}
Met with an already infected person.................4282
Calculating for infected person: 237 of 22774
List of people this infector meets: {1}
Met with an already infected person.................4290
Calculating for infected person: 238 of 22774
List of people this infector meets: {1}
Met with an already infected person.................4295
Calculating for infected person: 239 of 22774
List of people this infector meets: {1}
Met with an already infected person.................4299
Calculating for infected person: 240 of 22774
List of people this infector meets: {1}
Met with an already infected person.................4310
Calculating for infected person: 241 of 22774
List of people this infector meets: {1}
Met with an already infected person.................4341
Calculating for infected person: 242 of 22774

...

List of people this infector meets: {4}
Met with an already infected person.................204762
Met with an already infected person.................204763
Met with an already infected person.................204766
Non infected person met.................204784
Calculating for infected person: 233 of 244
List of people this infector meets: {4}
Met with an already infected person.................204762
Met with an already infected person.................204763
Met with an already infected person.................204766
Met with an already infected person.................204784
Calculating for infected person: 234 of 244
List of people this infector meets: {6}
Met with an already infected person.................204762
Met with an already infected person.................204763
Met with an already infected person.................204766
Met with an already infected person.................204784
Non infected person met.................204789
Non infected person met.................204794
Ca

List of people this infector meets: {14}
Met with an already infected person.................50443
Met with an already infected person.................50456
Met with an already infected person.................50458
Met with an already infected person.................50482
Met with an already infected person.................50502
Met with an already infected person.................50550
Met with an already infected person.................50560
Met with an already infected person.................50593
Met with an already infected person.................50681
Met with an already infected person.................50685
Met with an already infected person.................50701
Met with an already infected person.................50715
Met with an already infected person.................50742
Met with an already infected person.................50762
Calculating for infected person: 17 of 83
List of people this infector meets: {17}
Met with an already infected person.................50456
Met wi

Calculating for infected person: 46 of 83
List of people this infector meets: {7}
Met with an already infected person.................169353
Met with an already infected person.................169355
Met with an already infected person.................169366
Met with an already infected person.................169380
Met with an already infected person.................169401
Met with an already infected person.................169407
Met with an already infected person.................169411
Calculating for infected person: 47 of 83
List of people this infector meets: {5}
Met with an already infected person.................169366
Met with an already infected person.................169380
Met with an already infected person.................169401
Met with an already infected person.................169407
Met with an already infected person.................169411
Calculating for infected person: 48 of 83
List of people this infector meets: {5}
Met with an already infected person...........

Calculating for infected person: 8 of 28
List of people this infector meets: {3}
Met with an already infected person.................67929
Met with an already infected person.................67930
Met with an already infected person.................67980
Calculating for infected person: 9 of 28
List of people this infector meets: {1}
Met with an already infected person.................80912
Calculating for infected person: 10 of 28
List of people this infector meets: {4}
Met with an already infected person.................85880
Met with an already infected person.................85940
Met with an already infected person.................85989
Met with an already infected person.................86005
Calculating for infected person: 11 of 28
List of people this infector meets: {7}
Non infected person met.................86303
Met with an already infected person.................86341
Met with an already infected person.................86396
Met with an already infected person.............

Non infected person met.................169546
Non infected person met.................169547
Calculating for infected person: 5 of 19
List of people this infector meets: {1}
Met with an already infected person.................170152
Calculating for infected person: 6 of 19
List of people this infector meets: {9}
Met with an already infected person.................172041
Met with an already infected person.................172044
Met with an already infected person.................172087
Met with an already infected person.................172109
Met with an already infected person.................172115
Met with an already infected person.................172117
Met with an already infected person.................172133
Met with an already infected person.................172135
Met with an already infected person.................172150
Calculating for infected person: 7 of 19
List of people this infector meets: {9}
Met with an already infected person.................181449
Met with an al

In [9]:
#Check number of infection rounds
len(infection_list)

10

In [10]:
# Check number of infections per round
y = [len(x) for x in infection_list]
y


[117, 605, 179, 66, 27, 18, 11, 7, 4, 0]

In [11]:
# Total infected individuals 
sum(y)

1034

In [12]:
# Write infected dataframe to the file
df.to_csv("NYCInfectedTMSC2014.tsv", sep="\t")

# Visualization
Geographic visualization of new infections at each iteration. Discrete and heat maps are displayed.

In [13]:
df = pd.read_csv("NYCInfectedTMSC2014.tsv",sep='\t', engine="python")
df.drop(["Unnamed: 0"],axis=1, inplace=True)

gis = GIS()

In [14]:
df

User ID (anonymized)     Venue ID (Foursquare)  \
0                        470  49bbd6c0f964a520f4531fe3   
1                        979  4a43c0aef964a520c6a61fe3   
2                         69  4c5cc7b485a1e21e00d35711   
3                        395  4bc7086715a7ef3bef9878da   
4                         87  4cf2c5321d18a143951b5cec   
...                      ...                       ...   
227423                   688  3fd66200f964a52000e71ee3   
227424                   560  4bca32ff0687ef3be789dbcc   
227425                   945  50a77716e4b0b5a9492f6f56   
227426                   671  4514efe0f964a520e7391fe3   
227427                   942  4a1e0ca0f964a520bf7b1fe3   

       Venue category ID (Foursquare) Venue category name (Fousquare)  \
0            4bf58dd8d48988d127951735             Arts & Crafts Store   
1            4bf58dd8d48988d1df941735                          Bridge   
2            4bf58dd8d48988d103941735                  Home (private)   
3            4bf58dd8d48988d104941735                  Medical Center   
4            4bf58dd8d48988d1cb941735                      Food Truck   
...                               ...                             ...   
227423       4bf58dd8d48988d1e7931735                     Music Venue   
227424       4bf58dd8d48988d16c941735                    Burger Joint   
227425       4bf58dd8d48988d103941735                  Home (private)   
227426       4bf58dd8d48988d11d941735                             Bar   
227427       4bf58dd8d48988d116941735                             Bar   

         Latitude  Longitude  Timezone offset(minutes)  \
0       40.719810 -74.002581                      -240   
1       40.606800 -74.044170                      -240   
2       40.716162 -73.883070                      -240   
3       40.745164 -73.982519                      -240   
4       40.740104 -73.989658                      -240   
...           ...        ...                       ...   
227423  40.733596 -74.003139                      -300   
227424  40.745719 -73.993720                      -300   
227425  40.854364 -73.883070                      -300   
227426  40.735981 -74.029309                      -300   
227427  40.726805 -73.957422                      -300   

                              UTC time  Status  Iteration  InfectorId  \
0       Tue Apr 03 18:00:09 +0000 2012       0          0           0   
1       Tue Apr 03 18:00:25 +0000 2012       0          0           0   
2       Tue Apr 03 18:02:24 +0000 2012       0          0           0   
3       Tue Apr 03 18:02:41 +0000 2012       0          0           0   
4       Tue Apr 03 18:03:00 +0000 2012       0          0           0   
...                                ...     ...        ...         ...   
227423  Sat Feb 16 02:29:11 +0000 2013       0          0           0   
227424  Sat Feb 16 02:31:35 +0000 2013       0          0           0   
227425  Sat Feb 16 02:33:16 +0000 2013       0          0           0   
227426  Sat Feb 16 02:34:31 +0000 2013       0          0           0   
227427  Sat Feb 16 02:35:36 +0000 2013       0          0           0   

        InfectionTime        Time  InfectionLongitude  InfectionLatitude  
0                   0  1333476009                 NaN                NaN  
1                   0  1333476025                 NaN                NaN  
2                   0  1333476144                 NaN                NaN  
3                   0  1333476161                 NaN                NaN  
4                   0  1333476180                 NaN                NaN  
...               ...         ...                 ...                ...  
227423              0  1360981751                 NaN                NaN  
227424              0  1360981895                 NaN                NaN  
227425              0  1360981996                 NaN                NaN  
227426              0  1360982071                 NaN                NaN  
227427              0  1360982136  

In [15]:
print(infection_list[0])

[ 503  666  601 1071  615  217  314  397  316  315  481  221  563  894
  751   54   65  195   46  438  371 1013  874  941  564  169 1042  328
  198  906 1002  300  433  834  265  207  598 1009   10   61  391  540
  377  478  541 1080  507  376  241  310  116  705  403  261  309   40
  176  624  744  226  491  251 1028  284  737  777  330  897  108  132
  332 1011  973  361  295  695 1069  974  953  203 1033  745   94  453
   18  175  859  269  466   42  929  385  326   31 1004  442  447  748
  490  928  932  583  137  676  875   41  821  595  165  960  761  743
  488 1035  542  587    6]


In [16]:
df.shape

(227428, 15)

In [17]:
df.columns

Index(['User ID (anonymized)', 'Venue ID (Foursquare)',
       'Venue category ID (Foursquare)', 'Venue category name (Fousquare)',
       'Latitude', 'Longitude', 'Timezone offset(minutes)', 'UTC time',
       'Status', 'Iteration', 'InfectorId', 'InfectionTime', 'Time',
       'InfectionLongitude', 'InfectionLatitude'],
      dtype='object')

# Plot new and unique infections

In [96]:
iteration = 1
infected_df = df[df["Status"]==1 & (df["Iteration"]==iteration)]

In [97]:
infected_df.shape

(204256, 15)

## Visualize Spatially
Convert to Spatially Enabled DataFrame

# IMPORTANT: Load maps one-by-one by running the cell pairs for rendering maps, for example (both of these cells need to be ezecuted in order for the maps to render with spatial plots):
Cell 1:
```
pdx_map_nyc = gis.map('New York City, NY')
pdx_map_nyc.basemap = 'topo'
pdx_map_nyc
```

Cell 2:
```
infected_df.spatial.plot(map_widget=pdx_map_nyc)
```

Source: https://developers.arcgis.com/python/guide/install-and-set-up/
The map widget is only supported within Jupyter applications. Follow these additional steps to use the map widget in a disconnected environment:

    install the jupyterlab package for visualizing with maps in either Jupyter Notebook or Jupyter Lab:

    conda install jupyterlab

    enable the map widget by running these 2 commands in succession:

        jupyter nbextension enable --py --sys-prefix widgetsnbextension

        jupyter nbextension enable --py --sys-prefix arcgis


In [20]:
sdf = pd.DataFrame.spatial.from_xy(infected_df, 'Longitude','Latitude')
type(sdf)

/opt/anaconda3/envs/cs293b/lib/python3.7/site-packages/arcgis/features/geo/_io/fileops.py:150: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['SHAPE'] = geoms
/opt/anaconda3/envs/cs293b/lib/python3.7/site-packages/pandas/core/indexing.py:966: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s
/opt/anaconda3/envs/cs293b/lib/python3.7/site-packages/arcgis/features/geo/_accessor.py:1021: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[r

pandas.core.frame.DataFrame

In [21]:
pdx_map_nyc = gis.map('New York City, NY')
pdx_map_nyc.basemap = 'topo'
pdx_map_nyc

MapView(layout=Layout(height='400px', width='100%'))

In [24]:
infected_df.spatial.plot(map_widget=pdx_map_nyc)

True

In [25]:
pdx_map_tko = gis.map('Tokyo')
pdx_map_tko.basemap = 'topo'
pdx_map_tko

MapView(layout=Layout(height='400px', width='100%'))

In [26]:
infected_df.spatial.plot(map_widget=pdx_map_tko)

True

## Explore density of infections
These heatmaps may take a couple minutes to render

In [27]:
pdx_density_map_nyc = gis.map('New York City, NY')
pdx_density_map_nyc.basemap='gray'
pdx_density_map_nyc

MapView(layout=Layout(height='400px', width='100%'))

In [28]:
infected_df.spatial.plot(map_widget=pdx_density_map_nyc, renderer_type='h')

True

## Plot cumulative infections

## Cumulative infections at iteration 0

In [80]:
infected_df = df[(df["Status"]==1) & (df["Iteration"] == 0)]
infected_df

User ID (anonymized)     Venue ID (Foursquare)  \
1999                     503  4ea073e3cc21b2fa8ecb3a6e   
2001                     503  4d6d976d792bb60cbdd156be   
2002                     666  4a8108a0f964a52095f61fe3   
2013                     601  40b68100f964a5207d001fe3   
2036                    1071  4a525e9df964a52094b11fe3   
...                      ...                       ...   
227380                   314  50c3cbbce4b085c8e4119be8   
227381                   875  49f47a7af964a5200a6b1fe3   
227397                   542  4be1db7dedbb0f47c5eaa615   
227415                   737  4a73515ef964a5201edc1fe3   
227416                   751  41005500f964a5204e0b1fe3   

       Venue category ID (Foursquare) Venue category name (Fousquare)  \
1999         4bf58dd8d48988d162941735            Other Great Outdoors   
2001         4bf58dd8d48988d1c1941735              Mexican Restaurant   
2002         4bf58dd8d48988d176941735            Gym / Fitness Center   
2013         4bf58dd8d48988d163941735                            Park   
2036         4bf58dd8d48988d121941735                             Bar   
...                               ...                             ...   
227380       4d954b0ea243a5684a65b473               Convenience Store   
227381       4bf58dd8d48988d120941735                             Bar   
227397       4bf58dd8d48988d1a3941735       College Academic Building   
227415       4bf58dd8d48988d1f8941735          Furniture / Home Store   
227416       4bf58dd8d48988d116941735                             Bar   

         Latitude  Longitude  Timezone offset(minutes)  \
1999    40.642926 -74.014155                      -240   
2001    40.641934 -74.013622                      -240   
2002    40.762959 -73.915591                      -240   
2013    40.742188 -73.987924                      -240   
2036    40.754018 -73.984532                      -240   
...           ...        ...                       ...   
227380  40.749021 -74.136357                      -300   
227381  40.749443 -73.984865                      -300   
227397  40.776677 -73.980567                      -300   
227415  40.715722 -74.011751                      -300   
227416  40.666674 -73.988171                      -300   

                              UTC time  Status  Iteration  InfectorId  \
1999    Wed Apr 04 17:17:34 +0000 2012       1          0           0   
2001    Wed Apr 04 17:17:54 +0000 2012       1          0           0   
2002    Wed Apr 04 17:18:21 +0000 2012       1          0           0   
2013    Wed Apr 04 17:25:03 +0000 2012       1          0           0   
2036    Wed Apr 04 17:34:22 +0000 2012       1          0           0   
...                                ...     ...        ...         ...   
227380  Sat Feb 16 01:42:05 +0000 2013       1          0           0   
227381  Sat Feb 16 01:43:57 +0000 2013       1          0           0   
227397  Sat Feb 16 02:02:48 +0000 2013       1          0           0   
227415  Sat Feb 16 02:18:49 +0000 2013       1          0           0   
227416  Sat Feb 16 02:19:07 +0000 2013       1          0           0   

        InfectionTime        Time  InfectionLongitude  InfectionLatitude  
1999       1333559854  1333559854                 NaN                NaN  
2001       1333559854  1333559874                 NaN                NaN  
2002       1333559854  1333559901                 NaN                NaN  
2013       1333559854  1333560303                 NaN                NaN  
2036       1333559854  1333560862                 NaN                NaN  
...               ...         ...                 ...                ...  
227380     1333559854  1360978925                 NaN                NaN  
227381     1333559854  1360979037                 NaN                NaN  
227397     1333559854  1360980168                 NaN                NaN  
227415     1333559854  1360981129                 NaN                NaN  
227416     1333559854  1360981147  

In [70]:
sdf = pd.DataFrame.spatial.from_xy(infected_df, 'Longitude','Latitude')
pdx_map_nyc = gis.map('New York City, NY')
pdx_map_nyc.basemap = 'topo'
pdx_map_nyc

MapView(layout=Layout(height='400px', width='100%'))

In [71]:
infected_df.spatial.plot(map_widget=pdx_map_nyc)

True

### Explore density of infections for cumulative infections (Iteration 0)

In [72]:
pdx_density_map_nyc = gis.map('New York City, NY')
pdx_density_map_nyc.basemap='gray'
pdx_density_map_nyc

MapView(layout=Layout(height='400px', width='100%'))

In [73]:
infected_df.spatial.plot(map_widget=pdx_density_map_nyc, renderer_type='h')

True

## Cumulative infections from iteration 0-total iteration count

In [77]:
infected_df = df[(df["Status"]==1) & (df["Iteration"] <= iteration_count)]
infected_df.shape

(24816, 15)

In [75]:
sdf = pd.DataFrame.spatial.from_xy(infected_df, 'Longitude','Latitude')
pdx_map_nyc = gis.map('New York City, NY')
pdx_map_nyc.basemap = 'topo'
pdx_map_nyc

MapView(layout=Layout(height='400px', width='100%'))

In [76]:
infected_df.spatial.plot(map_widget=pdx_map_nyc)

True

### Explore density of infections for cumulative infections (Iteration 0-total iteration count)

In [67]:
pdx_density_map_nyc = gis.map('New York City, NY')
pdx_density_map_nyc.basemap='gray'
pdx_density_map_nyc

MapView(layout=Layout(height='400px', width='100%'))

In [68]:
infected_df.spatial.plot(map_widget=pdx_density_map_nyc, renderer_type='h')

True